In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list the files in the input directory

import os
print(os.listdir("../input"))

# Any results you write to the current directory are saved as output.

['embeddings', 'train.csv', 'sample_submission.csv', 'test.csv']


In [2]:
train=pd.read_csv('../input/train.csv')
test=pd.read_csv('../input/test.csv')



In [11]:
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(train["question_text"], train["target"], test_size=0.08, random_state=2018,stratify= train["target"])
print(X_train)
print("DONE")

841134     What are some ways to get some alone time as a...
819280              What can I do if I have rats in my yard?
491496     If a narcissist devalues and discards does it ...
888186     How can we know that a person is online on Ins...
494315     How much time will a new retail business take ...
1712       Is it true that Hitler and Mao helped prevent ...
443390                               Can you be too healthy?
768711     Are there any animals as dependent on their pa...
902103     Do you think Obama is the worst President and ...
440118             What are the uses of cow, buffolo, sheep?
27828      What does it mean when ex says, "you are a gre...
749015                              What is your daily plan?
977962           How do I get all active numbers in my city?
999780     Why does Western Europe (especially Germany) p...
835235     What is a 'spin-off book' by a vlogger? And wh...
1267055    What are some offensive/banned words in Parlia...
741038       Should an a

In [12]:
from tensorflow.python.keras.preprocessing.text import Tokenizer
from tensorflow.python.keras.preprocessing.sequence import pad_sequences


tokenizer_obj = Tokenizer()
total_reviews=pd.concat([X_train, X_test], axis=0)
tokenizer_obj.fit_on_texts(total_reviews)

max_length=max([len(s.split()) for s in total_reviews])
vocab_size = len(tokenizer_obj.word_index)+1
print(max_length)
print(vocab_size)
X_train_tokens=tokenizer_obj.texts_to_sequences(X_train)
X_test_tokens=tokenizer_obj.texts_to_sequences(X_test)

X_train_pad=pad_sequences(X_train_tokens,maxlen=max_length,padding='post')
X_test_pad=pad_sequences(X_test_tokens,maxlen=max_length,padding='post')

134
222162


In [3]:
import tensorflow as tf
from keras import backend as K
def f1(y_true, y_pred):
    y_pred = K.round(y_pred)
    tp = K.sum(K.cast(y_true*y_pred, 'float'), axis=0)
    tn = K.sum(K.cast((1-y_true)*(1-y_pred), 'float'), axis=0)
    fp = K.sum(K.cast((1-y_true)*y_pred, 'float'), axis=0)
    fn = K.sum(K.cast(y_true*(1-y_pred), 'float'), axis=0)

    p = tp / (tp + fp + K.epsilon())
    r = tp / (tp + fn + K.epsilon())

    f1 = 2*p*r / (p+r+K.epsilon())
    f1 = tf.where(tf.is_nan(f1), tf.zeros_like(f1), f1)
    return K.mean(f1)

def f1_loss(y_true, y_pred):
    
    tp = K.sum(K.cast(y_true*y_pred, 'float'), axis=0)
    tn = K.sum(K.cast((1-y_true)*(1-y_pred), 'float'), axis=0)
    fp = K.sum(K.cast((1-y_true)*y_pred, 'float'), axis=0)
    fn = K.sum(K.cast(y_true*(1-y_pred), 'float'), axis=0)

    p = tp / (tp + fp + K.epsilon())
    r = tp / (tp + fn + K.epsilon())

    f1 = 2*p*r / (p+r+K.epsilon())
    f1 = tf.where(tf.is_nan(f1), tf.zeros_like(f1), f1)
    return 1 - K.mean(f1)
def bce_f1_loss(y_true,y_pred):
    return 0.5*K.binary_crossentropy(y_true,y_pred)+0.5*f1_loss(y_true,y_pred)

Using TensorFlow backend.


In [ ]:

from keras.layers import Input, Dense, concatenate, Activation,Conv1D,GlobalMaxPooling1D,Dropout,GaussianNoise
from keras.models import Model

tweet_input = Input(shape=(max_length,), dtype='int32')
#weights=[embedding_matrix],
tweet_encoder = Embedding(vocab_size, EMBEDDING_DIM,  input_length=max_length, trainable=True)(tweet_input)
bigram_branch = Conv1D(filters=100, kernel_size=2, padding='valid', activation='relu', strides=1)(tweet_encoder)
bigram_branch = GlobalMaxPooling1D()(bigram_branch)
trigram_branch = Conv1D(filters=100, kernel_size=3, padding='valid', activation='relu', strides=1)(tweet_encoder)
trigram_branch = GlobalMaxPooling1D()(trigram_branch)
fourgram_branch = Conv1D(filters=100, kernel_size=4, padding='valid', activation='relu', strides=1)(tweet_encoder)
fourgram_branch = GlobalMaxPooling1D()(fourgram_branch)
merged = concatenate([bigram_branch, trigram_branch, fourgram_branch], axis=1)

merged = Dense(256, activation='relu')(merged)
merged = Dropout(0.2)(merged)
merged = Dense(1)(merged)
output = Activation('sigmoid')(merged)
model = Model(inputs=[tweet_input], outputs=[output])
model.compile(loss=bce_f1_loss,
                  optimizer='adam',
                  metrics=['accuracy','binary_crossentropy',f1_loss])
model.summary()

In [4]:
EMBEDDING_DIM=100

import string
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

review_lines=list()
lines=train["question_text"].values.tolist()

for line in lines:
    tokens = word_tokenize(line)
    tokens = [w.lower() for w in tokens]
    table = str.maketrans('','',string.punctuation)
    stripped = [w.translate(table) for w in tokens]
    words = [word for word in stripped if word.isalpha()]
    stop_words=set(stopwords.words('english'))
    words=[w for w in words if not w in stop_words]
    review_lines.append(words)
    
print("done")    

done


In [5]:
import gensim

model=gensim.models.Word2Vec(sentences=review_lines,size=EMBEDDING_DIM,window=5,workers=4,min_count=1)
words=list(model.wv.vocab)
print(len(words))

216316


In [6]:
file_name="./custw2v.txt"
model.wv.save_word2vec_format(file_name,binary=False)
print("DONE")

DONE


In [7]:
import os
embeddings_index={}
f=open(file_name,encoding='utf8')
for line in f:
    values=line.split()
    word=values[0]
    coefs=np.asarray(values[1:])
    embeddings_index[word]=coefs
f.close()
print(len(embeddings_index))
print("DONE")

216317
DONE


In [21]:
from tensorflow.python.keras.preprocessing.text import Tokenizer
from tensorflow.python.keras.preprocessing.sequence import pad_sequences
tokenizer_obj = Tokenizer()
tokenizer_obj.fit_on_texts(review_lines)
sequences=tokenizer_obj.texts_to_sequences(review_lines)

word_index=tokenizer_obj.word_index

review_pad=pad_sequences(sequences,maxlen=max_length)
sentiment=train["target"].values
print("DONE")

DONE


In [22]:



num_words=len(word_index)+1

embedding_matrix=np.zeros((num_words,EMBEDDING_DIM))
print(len(embedding_matrix))
for word,i in word_index.items():
    if i > num_words:
        continue
    embedding_vector=embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i]=embedding_vector

print(len(embedding_matrix))
print("DONE")

{'get': 1, 'would': 2, 'best': 3, 'people': 4, 'like': 5, 'nt': 6, 'good': 7, 'one': 8, 'india': 9, 'make': 10, 'think': 11, 'many': 12, 'much': 13, 'time': 14, 'someone': 15, 'life': 16, 'use': 17, 'way': 18, 'know': 19, 'us': 20, 'want': 21, 'work': 22, 'take': 23, 'ever': 24, 'find': 25, 'world': 26, 'could': 27, 'become': 28, 'without': 29, 'person': 30, 'feel': 31, 'better': 32, 'quora': 33, 'year': 34, 'go': 35, 'trump': 36, 'new': 37, 'possible': 38, 'job': 39, 'years': 40, 'mean': 41, 'indian': 42, 'women': 43, 'used': 44, 'need': 45, 'start': 46, 'first': 47, 'difference': 48, 'money': 49, 'still': 50, 'different': 51, 'country': 52, 'really': 53, 'school': 54, 'learn': 55, 'business': 56, 'long': 57, 'love': 58, 'things': 59, 'college': 60, 'even': 61, 'old': 62, 'engineering': 63, 'give': 64, 'help': 65, 'online': 66, 'say': 67, 'day': 68, 'see': 69, 'using': 70, 'bad': 71, 'men': 72, 'book': 73, 'university': 74, 'company': 75, 'ca': 76, 'back': 77, 'change': 78, 'anyone': 

216317
DONE


In [31]:
from keras.initializers import Constant

from keras.layers import Input, Dense, concatenate, Activation,Conv1D,GlobalMaxPooling1D,Dropout,GaussianNoise,Embedding,GRU
from keras.models import Model,Sequential

model=Sequential()
embedding_layer=Embedding(num_words,EMBEDDING_DIM,embeddings_initializer=Constant(embedding_matrix), input_length=max_length,trainable=False)
model.add(embedding_layer)
model.add(GRU(units=32,dropout=0.3,recurrent_dropout=0.3))
model.add(Dense(1,activation="sigmoid"))
model.compile(loss=bce_f1_loss,optimizer="adam",metrics=["acc",f1_loss])
model.summary()



_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_3 (Embedding)      (None, 134, 100)          21631700  
_________________________________________________________________
gru_2 (GRU)                  (None, 32)                12768     
_________________________________________________________________
dense_2 (Dense)              (None, 1)                 33        
Total params: 21,644,501
Trainable params: 12,801
Non-trainable params: 21,631,700
_________________________________________________________________


In [29]:
VALIDATION_SPLIT=0.08
indices=np.arange(review_pad.shape[0])
np.random.shuffle(indices)
review_pad=review_pad[indices]
sentiment=sentiment[indices]
num_val_samples=int(VALIDATION_SPLIT*review_pad.shape[0])

X_train_pad=review_pad[:-num_val_samples]
y_train=sentiment[:-num_val_samples]
X_test_pad=review_pad[-num_val_samples:]
y_test=sentiment[-num_val_samples:]
print("DONE")

In [ ]:
model.fit(X_train_pad,y_train,batch_size=1024,epochs=5,validation_data=(X_test_pad,y_test))

In [ ]:
from sklearn import metrics

pred_val_y_4 = model.predict(X_test_pad, batch_size=1024, verbose=1)
thresholds = []
for thresh in np.arange(0.01, 0.99, 0.01):
    thresh = np.round(thresh, 2)
    res = metrics.f1_score(y_test, (pred_val_y_4 > thresh).astype(int))
    thresholds.append([thresh, res])
    print("F1 score at threshold {0} is {1}".format(thresh, res))
    
thresholds.sort(key=lambda x: x[1], reverse=True)
best_thresh_4 = thresholds[0][0]
print("Best threshold: ", best_thresh_4)


In [ ]:
y_test=model.predict([x_test[0],predklabelTest], batch_size=1024, verbose=1)
y_te = (y_test[:,0] > best_thresh_4).astype(np.int)

submit_df = pd.DataFrame({"qid": test_df["qid"], "prediction": y_te})
submit_df.to_csv("submission.csv", index=False)